In [3]:
import os
from pyspark import SparkConf, SparkContext
f = open("/Users/mencher/Projects/big_data/Outputfile.txt", 'a')

# Report

根據題目，本次需進行 500x500 的 matrix 互乘，以下為本次實作的步驟：
1. 初始化 PySpark ，讀入檔案後，首先將檔案**逐行拆分**。由於測資的樣本格式為 \\( (M, 0, 0, 51) \\) ，需再依據**逗號**分隔並產生 Python List（如：[M, 0, 0, 51]），方便後續存取，並透過 flatMap 輸出 rdd 格式。

2. 接著，分出 M 的 Map 與 N 的 Map。對於每個 matrix \\( m_{ij} 、 n_{jk} \\) ，我們需要整理成以下格式：

> \\[M: (j, (M, i, (m_{ij}))\\]
> \\[N: (j, (N, k, (n_{jk}))\\]
> 以方便後續能用 \\( j \\) 進行 merge 。

3. 接續，我們要根據 key \\( j \\) ，將 M-Map 與 N-Map 進行整合。基本上任一個 \\( j \\)  ，都會找得到分別屬於 M-Map 的多項與 N-Map 的多項，兩者需互相交錯配對。我使用 \\( Join \\) Function 完成這個步驟， \\( Join \\) 能將有相同的 Key 值，來自 \\( M \\) 的 \\(  (M, i, (m_{ij})) \\) 與來自 \\( N \\) 的 \\(  (N, k, (n_{jk})) \\) 進行合併。同時，再透過下一個 map function，產生新的 key-value pair，讓新的 Key 為 \\( ( i, k ) \\) ，並讓新的 Value 為兩者的 product value  \\( m_{ij}n_{jk} \\) 。

4. 由於目前 matrix 中的任一 element ，已經整理出多個乘積，我用 reducer 進行 \\( x + y \\) 的計算，將所有乘積進行加總，得到本次作業的結果。

5. 因應輸出需求，將結果依據 key 值進行 sorting ，並寫到 output file。

In [4]:
# 1. First Step
conf = SparkConf().setMaster("local").setAppName("wordcount")
sc = SparkContext.getOrCreate(conf=conf)
splittedData = sc.textFile("./500input.txt").flatMap(lambda lines: [perLine.split(',') for perLine in lines.splitlines()])

# 2. Second Step
mMap = splittedData.filter(lambda val: val[0] == 'M').map(lambda val: (val[2], ('M', val[1], val[3])))
nMap = splittedData.filter(lambda val: val[0] == 'N').map(lambda val: (val[1], ('N', val[2], val[3])))

# 3. Third Step
midway_result = mMap.join(nMap).map(lambda val: ((val[1][0][1], val[1][1][1]), int(val[1][0][2])*int(val[1][1][2])))

# 4. Forth Step
result = midway_result.reduceByKey(lambda x, y: x + y)

# 5. Fifth Step
sorted_result = result.sortBy(lambda val: (int(val[0][0]), int(val[0][1])))
for item in sorted_result.collect():
    f.write('%s,%s,%d\n'%(item[0][0], item[0][1], item[1]))
    print('%s,%s,%d'%(item[0][0], item[0][1], item[1]))
f.close()
sc.stop()


0,0,1224217
0,1,1209205
0,2,1172528
0,3,1150746
0,4,1152989
0,5,1143435
0,6,1192906
0,7,1163613
0,8,1146928
0,9,1270345
0,10,1164367
0,11,1197043
0,12,1197989
0,13,1132939
0,14,1169192
0,15,1196336
0,16,1170027
0,17,1226865
0,18,1246305
0,19,1233307
0,20,1193495
0,21,1144991
0,22,1188082
0,23,1136498
0,24,1171027
0,25,1257640
0,26,1172161
0,27,1171267
0,28,1158241
0,29,1161176
0,30,1207314
0,31,1191679
0,32,1212365
0,33,1151200
0,34,1260592
0,35,1166960
0,36,1177580
0,37,1228129
0,38,1128280
0,39,1197121
0,40,1174699
0,41,1183543
0,42,1208107
0,43,1153855
0,44,1152943
0,45,1188817
0,46,1154121
0,47,1159208
0,48,1231126
0,49,1153542
0,50,1158492
0,51,1218339
0,52,1143906
0,53,1207696
0,54,1194344
0,55,1223763
0,56,1174863
0,57,1125549
0,58,1181720
0,59,1174469
0,60,1238751
0,61,1207042
0,62,1152540
0,63,1164662
0,64,1189808
0,65,1174461
0,66,1138804
0,67,1197535
0,68,1222778
0,69,1232397
0,70,1178505
0,71,1181059
0,72,1183000
0,73,1174073
0,74,1213413
0,75,1195465
0,76,1115773
0,77,1206

3,377,1245649
3,378,1313805
3,379,1320499
3,380,1327739
3,381,1279923
3,382,1336558
3,383,1301823
3,384,1280155
3,385,1276039
3,386,1178763
3,387,1295997
3,388,1256684
3,389,1219591
3,390,1226311
3,391,1237576
3,392,1290038
3,393,1302309
3,394,1271048
3,395,1308920
3,396,1190463
3,397,1223497
3,398,1271606
3,399,1267871
3,400,1248768
3,401,1268761
3,402,1223333
3,403,1219886
3,404,1236076
3,405,1178695
3,406,1292895
3,407,1318175
3,408,1261939
3,409,1203174
3,410,1152149
3,411,1284821
3,412,1239839
3,413,1240216
3,414,1312581
3,415,1185350
3,416,1276484
3,417,1238275
3,418,1323443
3,419,1245995
3,420,1255938
3,421,1258976
3,422,1227403
3,423,1246828
3,424,1269046
3,425,1196311
3,426,1277338
3,427,1213483
3,428,1254958
3,429,1205547
3,430,1236398
3,431,1250197
3,432,1251706
3,433,1301320
3,434,1301442
3,435,1214656
3,436,1324741
3,437,1225197
3,438,1257197
3,439,1254851
3,440,1290365
3,441,1187557
3,442,1277738
3,443,1285996
3,444,1272816
3,445,1240820
3,446,1295598
3,447,1295590
3,448,

6,376,1217110
6,377,1207212
6,378,1315022
6,379,1290229
6,380,1299825
6,381,1295434
6,382,1283519
6,383,1301301
6,384,1295724
6,385,1248214
6,386,1209695
6,387,1281495
6,388,1220693
6,389,1181607
6,390,1217240
6,391,1244373
6,392,1286887
6,393,1255582
6,394,1261043
6,395,1242988
6,396,1217615
6,397,1199331
6,398,1257283
6,399,1263240
6,400,1193513
6,401,1199425
6,402,1211066
6,403,1147842
6,404,1232393
6,405,1161722
6,406,1258723
6,407,1323235
6,408,1211691
6,409,1187337
6,410,1149699
6,411,1238424
6,412,1259596
6,413,1222414
6,414,1280271
6,415,1214273
6,416,1216419
6,417,1228898
6,418,1268233
6,419,1210321
6,420,1228889
6,421,1240030
6,422,1239489
6,423,1207217
6,424,1252404
6,425,1182527
6,426,1259512
6,427,1233928
6,428,1266040
6,429,1234298
6,430,1212418
6,431,1229575
6,432,1268634
6,433,1270307
6,434,1260506
6,435,1209950
6,436,1283770
6,437,1200460
6,438,1258842
6,439,1293680
6,440,1287997
6,441,1225344
6,442,1266317
6,443,1271555
6,444,1222314
6,445,1237043
6,446,1257833
6,447,

9,376,1205242
9,377,1188874
9,378,1329546
9,379,1248599
9,380,1281072
9,381,1291223
9,382,1290679
9,383,1266950
9,384,1240491
9,385,1200064
9,386,1170099
9,387,1217298
9,388,1223883
9,389,1189439
9,390,1199958
9,391,1224747
9,392,1291815
9,393,1259699
9,394,1260922
9,395,1275502
9,396,1162009
9,397,1219215
9,398,1263025
9,399,1278258
9,400,1208151
9,401,1204428
9,402,1191133
9,403,1205565
9,404,1230286
9,405,1138245
9,406,1240062
9,407,1297396
9,408,1234945
9,409,1153814
9,410,1132190
9,411,1220419
9,412,1209982
9,413,1182372
9,414,1291924
9,415,1203793
9,416,1213466
9,417,1219200
9,418,1278959
9,419,1204859
9,420,1230901
9,421,1199220
9,422,1243146
9,423,1229232
9,424,1219387
9,425,1252101
9,426,1268129
9,427,1218014
9,428,1192546
9,429,1214875
9,430,1201979
9,431,1215125
9,432,1254469
9,433,1270582
9,434,1273891
9,435,1196367
9,436,1251381
9,437,1196287
9,438,1246626
9,439,1229818
9,440,1270390
9,441,1179547
9,442,1247441
9,443,1229425
9,444,1232846
9,445,1227038
9,446,1218579
9,447,

12,376,1216683
12,377,1248907
12,378,1312000
12,379,1320122
12,380,1330262
12,381,1270990
12,382,1327134
12,383,1270856
12,384,1284372
12,385,1237526
12,386,1245990
12,387,1310550
12,388,1237930
12,389,1241680
12,390,1258592
12,391,1239677
12,392,1329133
12,393,1305914
12,394,1288800
12,395,1285787
12,396,1243684
12,397,1270678
12,398,1278284
12,399,1298402
12,400,1281125
12,401,1286611
12,402,1206296
12,403,1203318
12,404,1289824
12,405,1172175
12,406,1255794
12,407,1340014
12,408,1248101
12,409,1189889
12,410,1162983
12,411,1294376
12,412,1228138
12,413,1222828
12,414,1329933
12,415,1238811
12,416,1260263
12,417,1299379
12,418,1353166
12,419,1243716
12,420,1299803
12,421,1282728
12,422,1253557
12,423,1252040
12,424,1285046
12,425,1250970
12,426,1299532
12,427,1251954
12,428,1310328
12,429,1231503
12,430,1249933
12,431,1279993
12,432,1271820
12,433,1286604
12,434,1342713
12,435,1292116
12,436,1306716
12,437,1231386
12,438,1312312
12,439,1244420
12,440,1275474
12,441,1187526
12,442,128

...

490,484,1301728
490,485,1304969
490,486,1239436
490,487,1236439
490,488,1256974
490,489,1292243
490,490,1291280
490,491,1259611
490,492,1251038
490,493,1209515
490,494,1280692
490,495,1300977
490,496,1195641
490,497,1302441
490,498,1338320
490,499,1204716
491,0,1199675
491,1,1197434
491,2,1140859
491,3,1151326
491,4,1150582
491,5,1156726
491,6,1177048
491,7,1186641
491,8,1128580
491,9,1255340
491,10,1170449
491,11,1183864
491,12,1189627
491,13,1129906
491,14,1142469
491,15,1159376
491,16,1149994
491,17,1215497
491,18,1197928
491,19,1230750
491,20,1183755
491,21,1077860
491,22,1160989
491,23,1126743
491,24,1155710
491,25,1248703
491,26,1227806
491,27,1162387
491,28,1147337
491,29,1140078
491,30,1182152
491,31,1162964
491,32,1232100
491,33,1214243
491,34,1227770
491,35,1151765
491,36,1109205
491,37,1209937
491,38,1145917
491,39,1215105
491,40,1136831
491,41,1206734
491,42,1202449
491,43,1204916
491,44,1174422
491,45,1163781
491,46,1146339
491,47,1187408
491,48,1190203
491,49,1186000
491,

492,107,1204750
492,108,1259475
492,109,1252948
492,110,1277174
492,111,1238917
492,112,1226882
492,113,1231850
492,114,1293714
492,115,1172332
492,116,1218253
492,117,1169110
492,118,1283889
492,119,1232426
492,120,1254055
492,121,1148321
492,122,1248573
492,123,1209817
492,124,1285562
492,125,1182590
492,126,1176427
492,127,1212677
492,128,1259260
492,129,1263257
492,130,1261230
492,131,1229121
492,132,1165783
492,133,1248160
492,134,1221021
492,135,1212407
492,136,1254425
492,137,1293718
492,138,1260263
492,139,1177075
492,140,1230637
492,141,1238151
492,142,1201795
492,143,1240812
492,144,1232699
492,145,1270685
492,146,1312327
492,147,1229306
492,148,1242465
492,149,1300839
492,150,1263705
492,151,1258086
492,152,1241732
492,153,1214686
492,154,1253550
492,155,1161825
492,156,1255861
492,157,1242651
492,158,1276104
492,159,1262138
492,160,1251156
492,161,1277446
492,162,1238734
492,163,1258395
492,164,1227400
492,165,1251391
492,166,1239658
492,167,1209029
492,168,1245129
492,169,

495,216,1235031
495,217,1244748
495,218,1207627
495,219,1273664
495,220,1268776
495,221,1259387
495,222,1147969
495,223,1193464
495,224,1239771
495,225,1208897
495,226,1223720
495,227,1186144
495,228,1162600
495,229,1210902
495,230,1154833
495,231,1160376
495,232,1181992
495,233,1222228
495,234,1198088
495,235,1213554
495,236,1209648
495,237,1286987
495,238,1191274
495,239,1186540
495,240,1248410
495,241,1274016
495,242,1215902
495,243,1235425
495,244,1220635
495,245,1239765
495,246,1181443
495,247,1306527
495,248,1221349
495,249,1281617
495,250,1249421
495,251,1273204
495,252,1270778
495,253,1218766
495,254,1260321
495,255,1242535
495,256,1201328
495,257,1199716
495,258,1225873
495,259,1212599
495,260,1238434
495,261,1243848
495,262,1190395
495,263,1240578
495,264,1316498
495,265,1183758
495,266,1212999
495,267,1204065
495,268,1206397
495,269,1208585
495,270,1180914
495,271,1226579
495,272,1245390
495,273,1151698
495,274,1183897
495,275,1191110
495,276,1214439
495,277,1248306
495,278,

497,294,1213314
497,295,1272012
497,296,1240119
497,297,1326161
497,298,1293020
497,299,1272383
497,300,1247254
497,301,1223738
497,302,1198542
497,303,1248626
497,304,1275079
497,305,1215162
497,306,1254809
497,307,1173097
497,308,1251232
497,309,1196608
497,310,1308555
497,311,1271849
497,312,1270310
497,313,1278167
497,314,1235026
497,315,1245684
497,316,1246671
497,317,1255789
497,318,1261341
497,319,1237949
497,320,1254130
497,321,1210176
497,322,1281052
497,323,1243528
497,324,1275542
497,325,1179117
497,326,1245878
497,327,1326491
497,328,1270050
497,329,1229807
497,330,1190049
497,331,1268691
497,332,1271155
497,333,1292266
497,334,1272013
497,335,1238673
497,336,1274468
497,337,1178964
497,338,1208019
497,339,1272021
497,340,1233351
497,341,1249323
497,342,1262341
497,343,1238097
497,344,1306839
497,345,1214519
497,346,1216836
497,347,1253881
497,348,1208462
497,349,1318129
497,350,1243452
497,351,1267333
497,352,1269690
497,353,1290907
497,354,1267755
497,355,1252032
497,356,

499,438,1225450
499,439,1183692
499,440,1229321
499,441,1128599
499,442,1218958
499,443,1207759
499,444,1157261
499,445,1174633
499,446,1191381
499,447,1193101
499,448,1154221
499,449,1158842
499,450,1169113
499,451,1228775
499,452,1161031
499,453,1151124
499,454,1148588
499,455,1252271
499,456,1130211
499,457,1162003
499,458,1196607
499,459,1233464
499,460,1146238
499,461,1164681
499,462,1224246
499,463,1291983
499,464,1154130
499,465,1166156
499,466,1157151
499,467,1164744
499,468,1210578
499,469,1224604
499,470,1133155
499,471,1180504
499,472,1144507
499,473,1219119
499,474,1179246
499,475,1126112
499,476,1232161
499,477,1160040
499,478,1184785
499,479,1169525
499,480,1132848
499,481,1199893
499,482,1167962
499,483,1211171
499,484,1216019
499,485,1221706
499,486,1183745
499,487,1195896
499,488,1224647
499,489,1196555
499,490,1252120
499,491,1181855
499,492,1170894
499,493,1155734
499,494,1201754
499,495,1189996
499,496,1137334
499,497,1198548
499,498,1189622
499,499,1172100
